# Training RL Agent for given Number of Users for a single Server

In [24]:
import random
import pandas as pd
import numpy as np
np.set_printoptions(suppress=True)
import time

## Load Data for training
The dataset was generated using codes available in dataset_generator folder

In [25]:
datafile = 'dataset/dual_s_data.csv'
users_low = 100
users_res = 100
users_high = 500
#number_of_service = 2

#network latency
N_lat = 0.25

latency_threshold = 10 - N_lat #subtract latency due to network from total latency

1. states: RAM(MB), #Cores, BG WL(%), GPU(MB), S1:Users, S2:Users

2. More reward for the number closer to (s1,s2) with latency below given threshold

## RL Environment:

In [26]:
import numpy as np
import gym
from gym import spaces
from gym.utils import seeding


class yolosystem(gym.Env):
    metadata = {'render.modes': ['human']}
    
    def __init__(self, n_actions, filename):
        
        super(yolosystem, self).__init__()
        self.n_actions = n_actions #total number of action space after ranging [10, 20, 30 ...]
        self.action_space = spaces.Box(low=0, high=self.n_actions, shape=(1,), dtype=np.float32)
        #self.action_space = spaces.Discrete(self.n_actions) #total number of users in the action space; starts with zero
        
        self.observation_space = spaces.Box(low=np.array([0,0,0,0,0,0]), high=np.array([11000]*6), shape=(6, ), dtype=np.int32) #<RAM, Core, Workload>
        
        self.seed()
        self.current_obs = np.array( [3000, 2, 40, 2, 100, 100] ) #current observation = <ram, cores, workload%>

        #Load dataset
        self.df = pd.read_csv(filename)
        # computer percentage of GPU usage from actual use
        self.df['workload_gpu'] = self.df['workload_gpu'].multiply(1/80).round(0).astype(int) #round gpu workload

        #get unique data in set
        self.ram = self.df.ram.unique()
        self.cores = self.df.cores.unique()
        self.workload_cpu = self.df.workload_cpu.unique()
        print(self.df) #print dataset
       
        

    def seed(self, seed=1010):
        self.np_random, seed = seeding.np_random(seed)
        return [seed]

    def step(self, action):
#        print(action)
#        assert self.action_space.contains(action) #action should be in action space
        state = self.current_obs
        done = True #Episodes ends after each action

        #compute latecy from the number of users
        reward = self.get_reward(state, action) #linear latency           
#         print(action, reward)
        self.current_obs = self.get_random_state() #go to a random state
        
#        print(self.current_obs)
        return self.current_obs, reward, done, {} #no-states, reward, episode-done, no-info

    def reset(self):
        self.current_obs = self.get_random_state()
        return self.current_obs #current state of the system with no load

    def render(self, mode='human', close=False):
        print(f"Current State:<{self.current_obs}>")
        
    
    #compute latency
    def get_reward(self, state, action):
        #change action to users
        action = round(np.mean(action)) #take mean of np array
        u1 = action//5 + 1
        u2 = (action+1) - (u1-1)*5
        #sample time from dataframe
        gram = state[0]
        gcores = state[1]
        gwl_c = state[2]
        gwl_g = state[3]
        gs1 = u1*100
        gs2 = u2*100
#        print("user:", gs1, gs2, "act:", action)

        fetch_state = self.df.loc[ (self.df['ram'] == gram) & (self.df['cores']== gcores) & (self.df['workload_cpu']==gwl_c) & (self.df['workload_gpu']==gwl_g) & (self.df['users_yolo']==gs1) & (self.df['users_mnet']==gs2)]
                
        if fetch_state.empty:
            return -20 

        time1 = fetch_state.sample().iloc[0]['time_yolo'] #fetch time from the dataframe
        time2 = fetch_state.sample().iloc[0]['time_mnet']
        tm = max(time1, time2)
        #add total latencies due to network based on number of u1 and u2
        
        if (tm <= latency_threshold): 
            return  0.01*(gs1 - state[4]) +  0.01*(gs2 - state[5]) + u1 + u2 

        else:
            return -5 - u1 - u2     
        
    
    #get to some random state after taking an action
    def get_random_state(self):
        #generate state randomly
        gram = np.random.choice(self.ram, 1)[0]
        gcores = np.random.choice(self.cores, 1)[0]
        gwl_c = np.random.choice(self.workload_cpu, 1)[0]
        
        #fetch gamma for the state
        fetch_state = self.df.loc[ (self.df['ram'] == gram) & (self.df['cores']== gcores) & (self.df['workload_cpu']==gwl_c) ]
        gwl_g = fetch_state.sample().iloc[0]['workload_gpu'] #fetch workload randmoly
        
        gs1 = random.randrange(50, 550, 50)
        gs2 = random.randrange(50, 550, 50)
        
        return np.array( [gram, gcores, gwl_c, gwl_g, gs1, gs2] , dtype=np.int32)

## Test RL Environment with Baseline3

In [27]:
from stable_baselines3.common.env_checker import check_env
env = yolosystem( 25, datafile )
# If the environment don't follow the interface, an error will be thrown
check_env(env, warn=True)

        ram  cores  workload_cpu  workload_gpu  users_yolo  users_mnet  \
0      3000      2            40             2         100         100   
1      3000      2            40             2         100         200   
2      3000      2            40             2         100         300   
3      3000      2            40             2         100         400   
4      3000      2            40             2         100         500   
...     ...    ...           ...           ...         ...         ...   
5995  11000      5            60            10         500         100   
5996  11000      5            60            10         500         200   
5997  11000      5            60            10         500         300   
5998  11000      5            60            10         500         400   
5999  11000      5            60            10         500         500   

      time_yolo  time_mnet  
0     15.215310  17.846291  
1     15.477644  21.690610  
2     15.443997  27.3285

C:\Users\katek\anaconda3\envs\tf-gpu\lib\site-packages\stable_baselines3\common\env_checker.py:286: UserWarning: We recommend you to use a symmetric and normalized Box action space (range=[-1, 1]) cf https://stable-baselines3.readthedocs.io/en/master/guide/rl_tips.html
  warnings.warn(


In [28]:
print(env.observation_space)
print(env.action_space)
print(env.action_space.sample())

Box([0 0 0 0 0 0], [11000 11000 11000 11000 11000 11000], (6,), int32)
Box([0.], [25.], (1,), float32)
[17.94976]


In [29]:
for i in range(25):
    t = env.get_reward([3000, 2, 40, 2, 500, 500], i)
    print(t)

-7
-8
-9
-10
-11
-8
-9
-10
-11
-12
-9
-10
-11
-12
-13
-10
-11
-12
-13
-14
-11
-12
-13
-14
-15


In [30]:
n_steps = 10
for step in range(n_steps):
    print("Step {}".format(step + 1))
    obs, reward, done, info = env.step(env.action_space.sample())
    print('reward=', reward)
    env.render()

Step 1
reward= -9
Current State:<[3000    2   60    6  100  200]>
Step 2
reward= -11
Current State:<[11000     3    40     3   300   150]>
Step 3
reward= -11
Current State:<[11000     2    60     2   250   450]>
Step 4
reward= -8
Current State:<[3000    4   50    3  350  500]>
Step 5
reward= -12
Current State:<[3000    5   50    2  200  300]>
Step 6
reward= -10
Current State:<[11000     4    60     3   400   200]>
Step 7
reward= -10
Current State:<[7000    4   50    6  500  100]>
Step 8
reward= -12
Current State:<[5000    2   40    6  100  450]>
Step 9
reward= -20
Current State:<[9000    5   50    2  300  350]>
Step 10
reward= -10
Current State:<[7000    3   40    2  300   50]>


## Tensorboard for Training Status

In [31]:
from stable_baselines3.common.monitor import Monitor
import os
# Create log dir
log_dir = './agent_tensorboard/'
os.makedirs(log_dir, exist_ok=True)

env = Monitor(env, log_dir)

In [32]:
import gym
from stable_baselines3 import TD3
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise
from stable_baselines3.common.vec_env import DummyVecEnv

# wrap it
#env = gym.make(env)
env = DummyVecEnv([lambda: env])

# The noise objects for TD3
n_actions = env.action_space.shape[-1]
action_noise = NormalActionNoise(mean=np.zeros(n_actions), sigma=0.1 * np.ones(n_actions))

## Train RL Model

In [35]:
model = TD3("MlpPolicy", env, verbose=3, action_noise=action_noise, 
            tensorboard_log = log_dir, learning_starts=150000,  train_freq=30)

Using cpu device


In [ ]:
begin = time.time()
model.learn(total_timesteps=500000) #reset_num_timesteps=False
end = time.time()
training_time = end-begin

Logging to ./agent_tensorboard/TD3_8
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.2    |
| time/              |          |
|    episodes        | 4        |
|    fps             | 148      |
|    time_elapsed    | 0        |
|    total_timesteps | 4        |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.2    |
| time/              |          |
|    episodes        | 8        |
|    fps             | 203      |
|    time_elapsed    | 0        |
|    total_timesteps | 8        |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.7    |
| time/              |          |
|    episodes        | 12       |
|    fps             | 236      |
|    time_elapsed    | 0        |
|    total_

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.2    |
| time/              |          |
|    episodes        | 100      |
|    fps             | 308      |
|    time_elapsed    | 0        |
|    total_timesteps | 100      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.2    |
| time/              |          |
|    episodes        | 104      |
|    fps             | 311      |
|    time_elapsed    | 0        |
|    total_timesteps | 104      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.2    |
| time/              |          |
|    episodes        | 108      |
|    fps             | 310      |
|    time_elapsed    | 0        |
|    total_timesteps | 108      |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.4    |
| time/              |          |
|    episodes        | 200      |
|    fps             | 317      |
|    time_elapsed    | 0        |
|    total_timesteps | 200      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 204      |
|    fps             | 318      |
|    time_elapsed    | 0        |
|    total_timesteps | 204      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 208      |
|    fps             | 318      |
|    time_elapsed    | 0        |
|    total_timesteps | 208      |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 300      |
|    fps             | 324      |
|    time_elapsed    | 0        |
|    total_timesteps | 300      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 304      |
|    fps             | 324      |
|    time_elapsed    | 0        |
|    total_timesteps | 304      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 308      |
|    fps             | 324      |
|    time_elapsed    | 0        |
|    total_timesteps | 308      |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.6    |
| time/              |          |
|    episodes        | 400      |
|    fps             | 327      |
|    time_elapsed    | 1        |
|    total_timesteps | 400      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.7    |
| time/              |          |
|    episodes        | 404      |
|    fps             | 327      |
|    time_elapsed    | 1        |
|    total_timesteps | 404      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.7    |
| time/              |          |
|    episodes        | 408      |
|    fps             | 328      |
|    time_elapsed    | 1        |
|    total_timesteps | 408      |
--------------

...

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.5    |
| time/              |          |
|    episodes        | 67000    |
|    fps             | 348      |
|    time_elapsed    | 192      |
|    total_timesteps | 67000    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.5    |
| time/              |          |
|    episodes        | 67004    |
|    fps             | 348      |
|    time_elapsed    | 192      |
|    total_timesteps | 67004    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.5    |
| time/              |          |
|    episodes        | 67008    |
|    fps             | 348      |
|    time_elapsed    | 192      |
|    total_timesteps | 67008    |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 67100    |
|    fps             | 348      |
|    time_elapsed    | 192      |
|    total_timesteps | 67100    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 67104    |
|    fps             | 348      |
|    time_elapsed    | 192      |
|    total_timesteps | 67104    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.4    |
| time/              |          |
|    episodes        | 67108    |
|    fps             | 348      |
|    time_elapsed    | 192      |
|    total_timesteps | 67108    |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 67200    |
|    fps             | 348      |
|    time_elapsed    | 193      |
|    total_timesteps | 67200    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 67204    |
|    fps             | 348      |
|    time_elapsed    | 193      |
|    total_timesteps | 67204    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 67208    |
|    fps             | 348      |
|    time_elapsed    | 193      |
|    total_timesteps | 67208    |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.8    |
| time/              |          |
|    episodes        | 67300    |
|    fps             | 347      |
|    time_elapsed    | 193      |
|    total_timesteps | 67300    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.9    |
| time/              |          |
|    episodes        | 67304    |
|    fps             | 347      |
|    time_elapsed    | 193      |
|    total_timesteps | 67304    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.8    |
| time/              |          |
|    episodes        | 67308    |
|    fps             | 347      |
|    time_elapsed    | 193      |
|    total_timesteps | 67308    |
--------------

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | -11.3    |
| time/              |          |
|    episodes        | 67400    |
|    fps             | 347      |
|    time_elapsed    | 193      |
|    total_timesteps | 67400    |
---------------------------------


In [ ]:
training_time

In [ ]:
# Save the agent
model.save(f"td3_thres10")
# model.save(f"edge_agent_{latency_threshold}_lin")
# del model  # delete trained model to demonstrate loading

In [ ]:
# Load the trained agent
# from stable_baselines3 import DQN
# model = DQN.load("edge_agent_20_lin")
#return action and state
#model.predict(np.array([2000, 4, 30]), deterministic=True)